<a href="https://colab.research.google.com/github/MatthewFried/Udemy/blob/master/Foundation/_13_Looking_At_Data_Categorical_Example.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# load pandas and numpy libraries
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt
import missingno as msno
import seaborn as sns


df = pd.read_csv("https://raw.githubusercontent.com/MatthewFried/Udemy/master/Day3/Day3%20Data.csv", header=None,
                names=['symboling', 'normalized_losses', 'make', 'fuel_type','aspiration','num_of_doors',
                      'body_style','drive_wheels','engine_location','wheel_base','length','width',
                      'height','curb_weight','engine_type','num_of_cylinders','engine_size',
                      'fuel_system','bore','stroke','compression_ratio','horsepower','peak_rpm',
                      'city_mpg','highway_mpg','price'])


#create stored values in case we need to reference the original data
df2 = df
df_orignal = df

# check the dataset uploaded as expected
print(df.shape)
df.head()

(205, 26)


symboling normalized_losses         make  ... city_mpg highway_mpg  price
0          3                 ?  alfa-romero  ...       21          27  13495
1          3                 ?  alfa-romero  ...       21          27  16500
2          1                 ?  alfa-romero  ...       19          26  16500
3          2               164         audi  ...       24          30  13950
4          2               164         audi  ...       18          22  17450

[5 rows x 26 columns]

In [ ]:
!pip install pandas_profiling --upgrade

Requirement already up-to-date: pandas_profiling in /usr/local/lib/python3.6/dist-packages (2.9.0)


In [ ]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [ ]:
df.nunique()

symboling              6
normalized_losses     52
make                  22
fuel_type              2
aspiration             2
num_of_doors           3
body_style             5
drive_wheels           3
engine_location        2
wheel_base            53
length                75
width                 44
height                49
curb_weight          171
engine_type            7
num_of_cylinders       7
engine_size           44
fuel_system            8
bore                  39
stroke                37
compression_ratio     32
horsepower            60
peak_rpm              24
city_mpg              29
highway_mpg           30
price                187
dtype: int64

In [ ]:
sub_df = pd.DataFrame(df[['num_of_doors','drive_wheels','engine_location']])
sub_df.head()

num_of_doors drive_wheels engine_location
0          two          rwd           front
1          two          rwd           front
2          two          rwd           front
3         four          fwd           front
4         four          4wd           front

In [ ]:
#check for nulls
sub_df.isna().sum()

num_of_doors       0
drive_wheels       0
engine_location    0
dtype: int64

In [ ]:
#print all the unique values of my data
#we see that we have a question mark, and we need to get rid of that
for col in sub_df:
    print(sub_df[col].unique())

['two' 'four' '?']
['rwd' 'fwd' '4wd']
['front' 'rear']


In [ ]:
#get rid of question mark from num_of_doors column and convert to nan so that we have an easier time
sub_df['num_of_doors'] = sub_df['num_of_doors'].apply(lambda x: np.nan if x == '?' else x) 

#check if gone
print(sub_df['num_of_doors'].unique())

['two' 'four' nan]


In [ ]:
sub_df.isna().sum()

num_of_doors       2
drive_wheels       0
engine_location    0
dtype: int64

In [ ]:
#create a label encoder to turn the data into numbers
from sklearn import preprocessing

#set up LabelEncoding
le = preprocessing.LabelEncoder()

#the .astype(str) converts all the data to a string so that the NaNs are not a problem in the data
interim = le.fit_transform(sub_df['num_of_doors'].astype(str))

#check the classes used
print(list(le.classes_))

#check the converted values
le_name_mapping = dict(zip(le.classes_, le.transform(le.classes_)))
print(le_name_mapping)

['four', 'nan', 'two']
{'four': 0, 'nan': 1, 'two': 2}


In [ ]:
interim = pd.DataFrame(interim)
interim.columns = ['num_of_doors']
interim.head()

num_of_doors
0             2
1             2
2             2
3             0
4             0

In [ ]:
#put interim into a data frame in order to map the 1 to a np.nan
interim = pd.DataFrame(interim)

#rename the dataframe
interim.columns = ['num_of_doors']

#use a lambda to convert all instinces of a 1 back to a np.nan
interim['num_of_doors'] = interim['num_of_doors'].map(lambda x: np.nan if x in [1] else x)

#convert all cases of 2 to 1, because we only have 2 classes now
interim['num_of_doors'] = interim['num_of_doors'].map(lambda x: 1 if x in [2] else x)

#check that we were successful
print(interim['num_of_doors'].unique())

[ 1.  0. nan]


In [ ]:
#place interim ('num_of_doors') back in sub_df
sub_df['num_of_doors'] = interim


num_of_doors drive_wheels engine_location
0           1.0          rwd           front
1           1.0          rwd           front
2           1.0          rwd           front
3           0.0          fwd           front
4           0.0          4wd           front

In [ ]:
#use the KNNImputer on the data now
#this will convert the np.nan to a value that is closest to it
from sklearn.impute import KNNImputer

imputer = KNNImputer(n_neighbors=3)
interim = imputer.fit_transform(interim)

#after checking the new data, I see that the two values were imputed to 0.43842365
#since they can only be of one category I will switch it to 0 or 1 based on being above or below .5
interim[interim > .5] = 1
interim[interim <= .5] = 0


In [ ]:
#convert back to values now that we will set up get_dummies and we have finished imputing
doors = []

for k in interim:
  if k == 0:
    doors.append('four')
  else:
    doors.append('two')

#place it in a dataframe now
doors = pd.DataFrame(doors)
doors.columns = ['doors_of_car']

In [ ]:
#replace the fixed data with the original
sub_df['num_of_doors'] = doors['doors_of_car']
sub_df.head()

num_of_doors drive_wheels engine_location
0          two          rwd           front
1          two          rwd           front
2          two          rwd           front
3         four          fwd           front
4         four          4wd           front

#One Hot Encoding

First we use get_dummies to do one hot encoding.  This well help us with our categorical data.

In [ ]:
df_dummies = pd.get_dummies(sub_df)
df_dummies.head()

num_of_doors_four  ...  engine_location_rear
0                  0  ...                     0
1                  0  ...                     0
2                  0  ...                     0
3                  1  ...                     0
4                  1  ...                     0

[5 rows x 7 columns]

#OneHotEncoder

This is a special library that works similar to get_dummies, but it gives the user much more control. For instance, the handle_unknown will tell us if there is some issue with the data if we set to to 'error' instead of 'ignore'.  OneHotEncoder Encodes categorical integer features as a one-hot numeric array. It's transform method returns a sparse matrix if sparse=True else a 2-d array. You can't cast a 2-d array (or sparse matrix) into a Pandas Series. You must create a Pandas Series (a column in a Pandas dataFrame) for each category.  Instead, one could use LabelBinarizer (which is not recommended for larger datasets). See [here](https://stackoverflow.com/questions/36631163/what-are-the-pros-and-cons-between-get-dummies-pandas-and-onehotencoder-sciki) for more info.

In [ ]:
from sklearn.preprocessing import OneHotEncoder

#create the encoder.
encoder = OneHotEncoder(handle_unknown="ignore")

#only use on categorical features
encoder.fit(sub_df)

print(encoder.categories_)

[array(['four', 'two'], dtype=object), array(['4wd', 'fwd', 'rwd'], dtype=object), array(['front', 'rear'], dtype=object)]
<bound method OneHotEncoder.get_feature_names of OneHotEncoder(categories='auto', drop=None, dtype=<class 'numpy.float64'>,
              handle_unknown='ignore', sparse=True)>
